# Blind separasjon av signaler (Prosjekt 1 TMA4320)TMA4320 



## Innledning og teori

### Problemstilling

Problemstillingen tar utganspunkt i cocktailselskapproblemet, en situasjon hvor $n$ mikrofoner samler inn $n$ ulike miksede signaler fra $d$ ulike kilder. I dette tilfellet antas for enkelhets skyld $n = d$. Hvert opptak $x_i$ kan anses som en lineær kombinasjon av $d$ kilder $s_1, s_2, ..., s_n$, slik at

\begin{equation*}
x_i = a_{i1} \cdot s_i (t) + a_{i2} \cdot s_i(t) + ... + a_{id} \cdot s_i(t)
\end{equation*}

hvor miksematrisen $A = ((a_{ij}))$ er ukjent. I praksis er signalet digitalt, og $s_i(t)$ må sees som en sum av diskrete signaler 

\begin{equation*}
s_i(t) = s_i(t_1) + s_i(t_2) + ... + s_i(t_N), \quad t \in T.
\end{equation*}

Koden nedenfor bruker uavhengig kommponentanalyse til å approksimere den inverse av miksematrisen $A$, separeringsmatrisen $W$. Denne $W$ brukes til slutt på lydopptakene for å separere lydsignalene fra hverandre.

### Viktige antagelser

En viktig antagelse i uavhengig komponentanalyse er at kildene kan anses som statistisk uavhengige av hverandre, det vil si at for hvert enkelt tidspunkt $t$ vil alle $s_i(t)$ kunne anses som statistisk uavhengige av hverandre. I tillegg må det antas at de originale signalene er ikke-Gaussiske, altså at de ikke er normalfordelte. Da $x_i(t)$ er en lineær kombinasjon av $s$-verdier ved $N$ ulike $t$-er, der $N$ er et veldig stort tall, kan det antas at de registrerte signalen er mer Gaussiske enn kildene. 

### Beskrivelse av algoritmen

Ved å kreve at hvert signal har forventningsverdi 0, forenkles videre operasjoner. Miksematrisen sentreres ved at gjennnomsnittsverdien til hver rad i matrisen (hvert signal) trekkes fra hvert element i raden. Dermed summeres elementene i hver rad til 0, og denne operasjonen kalles sentrering.

Deretter transformeres signalene $x_i$ slik at de blir ukorrelerte med varians 1, $\tilde{x} = B x$, der $\tilde{x}$ er matrisen med de ukorrelerte signalene og $x$ er de originale signalene. Matrisen $B$ viser seg å være den inverse kvadratroten av kovariansmatrisen $C$, $C^{-1/2}$. Denne operasjonen kalles "whitening".


I siste steg maksimeres signalenes ikke-Gaussiskhet. Ikke-Gaussiskhet kan kvantiseres ved hjelp av Kurtose- eller Negentropyfunksjonen. 
\begin{equation*}
G_K(u) = 4u^3 , \quad G_N(u) = ue^{\frac{-u^2}{2}} .
\end{equation*}

Her er $G_K$ og $G_N$ funksjonene til henholdsvis Kurtose og Negentropy. Ved å kreve maksimal ikke-Gaussiskhet kan $W$ approksimeres iterativt. $W$ bør være ortogonal, og iterasjonen begynner med en tilfeldig valgt $W_0$. Lengden av hver rad i $W_0$ normaiseres til 1, slik som for ortogonale matriser. Iterasjonen har som formål at $W_{k+1}$ har større ikke-Gaussiskhet enn $W_k$. Et konvergenskriterium avslutter funksjonen, og en input-variabel max_iter avbryter itereringen dersom konvergens ikke oppnås.

### Konvergenskriterium

Konvergenskriteriet formuleres med utgangspunkt i matrisenes ortogonalitet. $\delta$ er et mål på hvor mye $W$ endrer seg på én iterasjon. Ved konvergens skal radene i den nye matrisen bli mer og mer parallelle med radene i den forrige, og skalarproduktene mellom radene nærmer seg 1, mens $\delta$ nærmer seg 0. Itereringen avbrytes ved å sette et toleransekrav $\delta \leq$ tol.

\begin{equation*} 
\delta = \displaystyle{\max_{1 \leq i \leq d}} \Bigg(1- \Bigg|\sum_{j=1}^d(W_k)_{ij}(  W_{k-1})_{ij}  \Bigg|\Bigg)
\end{equation*}

## Forberedelser

Koden nedenfor importerer data fra lydfiler audio/mix_1.wav, audio/mix_2.wav og audio/mix_3.wav. Se kommentarer i koden for detaljer.


In [2]:
"""De tre miksede lydfilene importeres. Her brukes ferdiglagede funksjoner fra det tilldelte biblioteket wav_file_loader.
Data fra lydfilene returneres som en matrise."""

import numpy as np
from wav_file_loader import read_wavefiles
from scipy.linalg import fractional_matrix_power

paths = ['audio/mix_1.wav', 'audio/mix_2.wav', 'audio/mix_3.wav']
data, sampling_rate = read_wavefiles(paths)
num_signals = data.shape[0]

paths2 = ['audio/everhadadream.wav', 'audio/kulsang.wav', 'audio/LangemannsSang.wav']
data2, sampling_rate2 = read_wavefiles(paths2)
num_signals2 = data2.shape[0]

In [3]:
"""Funksjonen normaliserer lydsignalenes volum, på denne måten får de tre signalene omtrent samme lydstyrke."""
def normalize_audio(data):
    """Skalér amplituden slik at max(data[i]) == 1"""
    abs_data = np.absolute(data)
    maximums = np.amax(abs_data,1)
    # Divide each row by a different vector element:
    data = data / maximums.reshape((3,1))
    return data 

data = normalize_audio(data)
data2 = normalize_audio(data2)

In [4]:
"""Her kan de opplastede lydklippene spilles av"""
import IPython.display as ipd

ipd.display(ipd.Audio(data[0,:], rate=sampling_rate))
ipd.display(ipd.Audio(data[1,:], rate=sampling_rate))
ipd.display(ipd.Audio(data[2,:], rate=sampling_rate))

ipd.display(ipd.Audio(data2[0,:], rate=sampling_rate2))
ipd.display(ipd.Audio(data2[1,:], rate=sampling_rate2))
ipd.display(ipd.Audio(data2[2,:], rate=sampling_rate2))

## Miksing
Denne delen om miksing, inkludert kodecellen nedenfor kan du foreløpig ignorere. Men dersom du seinere vil teste ut algoritmen ved å selv blande opplastede uavhengige signaler så kan funksjonene nedenfor komme til nytte.

In [5]:
def normalize_rowsums(A):
    """Divide each row in A by its sum.
    
    The sum of each row in the result is 1.0."""
    the_sum = np.sum(A,1)
    A = A / the_sum.reshape((3,1))
    return A

def random_mixing_matrix(signals, observations):
    """ Creates a random matrix
    
    Each element is a small positive number, not too close to 0.
    (1/11, 5/7).
    """
    A = 0.25 + np.random.rand(observations, signals)
    return normalize_rowsums(A)


In [6]:
A = random_mixing_matrix(num_signals, num_signals)
data_mixed = normalize_audio(A @ data2)

In [7]:
import IPython.display as ipd

ipd.display(ipd.Audio(data_mixed[0,:], rate=sampling_rate2))
ipd.display(ipd.Audio(data_mixed[1,:], rate=sampling_rate2))
ipd.display(ipd.Audio(data_mixed[2,:], rate=sampling_rate2))

## Preprosessering

Funksjonene nedenfor utfører preprosesseringsstegene beskrevet i innledningen. I hvert tilfelle er variabelen Z et numpy-array av dimensjon $3 \times N$ miksede signaler. 

In [8]:
def center_rows(Z):
    """ Tar in en (3 x N)-matrise Z og returnerer en sentrert (3 x N)-matrise, samt den vertikale vektoren mus, der hvert element
    er gjennomsnittet til radene 1, 2, ..., N. """
    mus = np.mean(Z, axis=1)
    Zc = Z - mus.reshape((3,1))
    return Zc, mus


def whiten_rows(Z):
    """ Funksjonen tar inn en sentrert matrise Z, og returnerer Z 'whitened', her Zw, hvor Zw = T * Z """
    C = np.cov(Z)  #lager kovariansmatrise C
    # De to neste trinnene beregner T (den inverse kvadratroten av C).
    U, S, _ = np.linalg.svd(C, full_matrices=False)
    T  = U @ np.diag(1 / np.sqrt(S)) @ U.T
    Zw = T @ Z
    return Zw


## Hovediterasjonen - maksimering av ikke-gaussiskhet

In [9]:
from sklearn.preprocessing import normalize

def normalize_rownorms(Z):
    """Funksjonen tar inn en matrise Z og returnerer matrisen Zn, hvor hver rad er normalisert."""
    Zn = normalize(Z, axis=1, norm='l1') # Skalerer hver rad i Z med normen
    return Zn




In [10]:
def decorrelate_weights(W):
    """Funksjonen ortogonaliserer (dekorrelerer) miksematrisen W. 
    Inputmatrisen W projiseres ned på en ortogonal matrise gjennom transformasjonen (WW^T)^{-1/2}W. 
    Funksjonen returner den projiserte W-matrisen."""
    return fractional_matrix_power(W @ W.T, -1/2) @ W
    



In [11]:
def G_k (s): # Her brukes Kurtosefunksjonen G som mål på ikke-Gaussiskhet
    G = 4*s**3 
    G_derrivative = 12*s**2 # Kurtosens deriverte
    return G, G_derrivative

def G_n (u): # Her brukes negentropyfunskjonen 
    G = u * np.exp(-u**2/2)
    G_derrivative = (1 - u**2) * np.exp(-u**2/2)
    return G, G_derrivative
 


def update_W(W_k, Zcw, f):
    
    """Beregner W_k+1 fra W_k.
    Input er en tifeldig (3 x 3)-matrise W_k, den sentrerte, 'whitened' (3 x N)-datamatrisen Zcw
    (kalt tilde{x} i innledningen) og kurtose- eller negentropyfunksjonen f. Funksjonen returnerer en optimalisert og ortogonalisert matrise W_{k+1}. """
    
    s = W_k @ Zcw
    G, G_derrivative = f(s)
    N = len(G[0])
    E_G = np.mean(G_derrivative, axis=1) # Finner forventningsverdien til den deriverte av kurtosen
    
    W_p = G @ Zcw.T/N - np.diag(E_G) @ W_k # Estimerer en matrise med større ikke-Gaussiskhet
    W_n = normalize_rownorms(W_p)
    W_no = decorrelate_weights(W_n)
    return W_no


    
    
    
    


In [12]:
def measure_of_convergence(W1, W2):
    """Tar inn to matriser (skal brukes til å ta inn matrisen fra forrige og nåværende iterasjon) og returnerer feilestimatet."""   
    delta = np.amax(1 - np.absolute(np.sum(W1*W2, axis=1)))
    return delta




In [13]:
import warnings
import numpy as np


def fast_ICA(Z, signals_to_find, f, tol=1e-12, max_iter=1000):
    """Funksjonen bruker funksjonene ovenfor til å behandle lydfilene, manipulere matriser,
    og optimere miksematrisen W gjennom iterasjon.

    Input: Z: ubehandlet data fra lydfilene
           signals_to_find: antall lydkilder, i vårt tilfelle alltid 3
           tol: toleranse for feilestimat
           max_iter: maksimalt antall iterasjoner dersom konvergens ikke oppnås
           f: kurtose- eller negentropyfunksjonen
    Output: Zcw: de separerte signalene
            W: den ferdigbehandlede miksematrisen W (3x3)
            Andre variabler, f. eks. antall iterasjoner, kan også hentes ut.
    """
    Zc, mus = center_rows(Z)
    Zcw = whiten_rows(Zc)
    W_0 = np.random.rand(3, 3) # Gir W_0 = W tilfeldig initialverdi 
    normalize_rownorms(W_0)    
    # Initialiserer variabler til bruk i while-løkka:
    W = update_W(W_0, Zcw, f)
    delta = measure_of_convergence(W_0, W)
    number_of_iterations = 0
    while delta > tol and number_of_iterations < max_iter:
        W_new = update_W(W, Zcw, f)
        delta = measure_of_convergence(W, W_new)
        W = W_new
        number_of_iterations += 1
    return number_of_iterations, W @ Zcw
    
    
iterations, signals = fast_ICA(data, num_signals, G_k) #kaller funksjonen med data fra lydfilene
print("Kurtosefunksjonen. Antall iterasjoner: ", iterations)

import IPython.display as ipd

"""Spiller av de separerte lydsignalene:"""

ipd.display(ipd.Audio(signals[0,:], rate=sampling_rate))
ipd.display(ipd.Audio(signals[1,:], rate=sampling_rate))
ipd.display(ipd.Audio(signals[2,:], rate=sampling_rate))


iterations, signals = fast_ICA(data, num_signals, G_n) #kaller funksjonen med data fra lydfilene
print("Negentropyfunksjonen. Antall iterasjoner: ", iterations)


"""Spiller av de separerte lydsignalene:"""

ipd.display(ipd.Audio(signals[0,:], rate=sampling_rate))
ipd.display(ipd.Audio(signals[1,:], rate=sampling_rate))
ipd.display(ipd.Audio(signals[2,:], rate=sampling_rate))



iterations, signals = fast_ICA(data2, num_signals, G_n) #kaller funksjonen med data fra lydfilene
print("Negentropyfunksjonen med egne klipp. Antall iterasjoner: ", iterations)


"""Spiller av de separerte lydsignalene:"""

ipd.display(ipd.Audio(signals[0,:], rate=sampling_rate2))
ipd.display(ipd.Audio(signals[1,:], rate=sampling_rate2))
ipd.display(ipd.Audio(signals[2,:], rate=sampling_rate2))

Kurtosefunksjonen. Antall iterasjoner:  8


Negentropyfunksjonen. Antall iterasjoner:  6


Negentropyfunksjonen med egne klipp. Antall iterasjoner:  7


## Avslutning
Basert på lydklippene over virker seperasjonsmetoden å fungere bra på de utdelte lydklippene. Det er fortsatt noe støy, spesielt i klippene hvor noen snakker, men det er likevel fullt mulig å høre hva som sies. Musikkfilen er mindre preget av støy. Denne forskjellen kan komme av at det er stillhet mellom ordene i taleklippene, slik at støyen som er der kommer tydelig frem. I musikkfilen er det kontinuerlig lyd som gjør det vanskeligere å høre støy. Det er svært liten forksjell på hvor godt lydfilene blir separert utifra om man velger å bruke Kurtose- eller Negentropyfunksjonen som mål på ikke-Gaussiskhet. Negentropyfunksjonen bruker ofte færre iterasjoner på å nå konvergenskriteriet. 

Koden vil fungere for alle lineært uavhengige (3x3) initialmatriser $W_0$. I teorien er det en mulighet for at radene i $W_0$ skal kunne bli lineært avhengige, men i praksis er ikke dette noe problem siden det skjer svært sjelden. Skulle det mot formodning skje kan koden kjøres på nytt. 

Egne lydfiler er importert og testet. Her blir Negentropyfunksjonen brukt. Seperasjonen av de egne lydklippene virker også å fungere bra, men det viser seg å være viktig at lydfilene er av 8 bit, samme frame rate og mono-lyd. 